To Store the scraped data in a SQL database

In [ ]:
! pip install mysql-connector-python
! pip install pandas

import pandas as pd
import mysql.connector
from tabulate import tabulate
from decimal import Decimal


#Store the Data in SQL DATABASE


In [2]:
# Connect to MySQL server
mydb = mysql.connector.connect(
    host="localhost",
    user="root",
    password="nithya",
    database="REDBUS"  
)
print("Database connection established.")

mycursor = mydb.cursor(buffered=True)
mydb.commit()
# Create the table if it doesn't exist
create_table_query =''' CREATE TABLE IF NOT EXISTS bus_details (
    ID INT AUTO_INCREMENT PRIMARY KEY,
    `Bus Name` VARCHAR(255),
    `Bus Type` VARCHAR(255),
    `Departure time` TIME,
    `Arrival time` TIME,
    `Total Duration` VARCHAR(255),
    `Rating` FLOAT,
    `Price` DECIMAL(10,2),
    `Seats Available` INT,
    `Route Name` VARCHAR(255),
    `Route Link` VARCHAR(255)
)
'''

mycursor.execute(create_table_query)
mydb.commit()

print("Table created successfully.")

# Load CSV file into DataFrame
df_All_BusDetails = pd.read_csv(r'F:\NITHYA ONLINE DATA SCIENCE\PROJECT REDBUS\All_BusDetails.csv')

# Clean DataFrame: Convert columns to appropriate types
df_All_BusDetails['Rating'] = pd.to_numeric(df_All_BusDetails['Rating'], errors='coerce')
df_All_BusDetails['Price'] = df_All_BusDetails['Price'].str.extract(r'(\d+\.?\d*)')[0].apply(lambda x: Decimal(x) if pd.notnull(x) else Decimal('0.0'))
df_All_BusDetails['Seats Available'] = df_All_BusDetails['Seats Available'].str.extract(r'(\d+)').fillna(0).astype(int)

# Fill NaN values with appropriate defaults
df_All_BusDetails.fillna({
    'Bus Name': '',
    'Bus Type': '',
    'Departure time': '00:00:00',
    'Arrival time': '00:00:00',
    'Total Duration': '',
    'Price': Decimal('0.0'),
    'Rating': 0
}, inplace=True)


# Prepare data for insertion
data_to_insert = df_All_BusDetails.to_records(index=False).tolist()


insert_query = '''
INSERT INTO bus_details (
    `Bus Name`, `Bus Type`, `Departure time`, `Arrival time`, `Total Duration`, 
    `Rating`, `Price`, `Seats Available`, `Route Name`, `Route Link`
) VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
'''

mycursor.executemany(insert_query, data_to_insert)
mydb.commit()

# Close the database connection
mycursor.close()
mydb.close()

print("Data inserted successfully.")


Database connection established.
Table created successfully.
Data inserted successfully.


In [3]:
print(tabulate(df_All_BusDetails, headers='keys', tablefmt='psql'))

+-------+-----------------------------------------------------------------------------------+--------------------------------------------------+------------------+----------------+------------------+----------+---------+-------------------+----------------------------------------------------+------------------------------------------------------------------------------+
|       | Bus Name                                                                          | Bus Type                                         | Departure time   | Arrival time   | Total Duration   |   Rating |   Price |   Seats Available | Route Name                                         | Route Link                                                                   |
|-------+-----------------------------------------------------------------------------------+--------------------------------------------------+------------------+----------------+------------------+----------+---------+-------------------+--------------

In [4]:
df_All_BusDetails.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14696 entries, 0 to 14695
Data columns (total 10 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   Bus Name         14696 non-null  object 
 1   Bus Type         14696 non-null  object 
 2   Departure time   14696 non-null  object 
 3   Arrival time     14696 non-null  object 
 4   Total Duration   14696 non-null  object 
 5   Rating           14696 non-null  float64
 6   Price            14696 non-null  object 
 7   Seats Available  14696 non-null  int32  
 8   Route Name       14696 non-null  object 
 9   Route Link       14696 non-null  object 
dtypes: float64(1), int32(1), object(8)
memory usage: 1.1+ MB
